# Proyecto Viz

In [3]:
import folium
from folium import plugins
from folium.plugins import HeatMapWithTime as HMWT
from folium.plugins import HeatMap as HM

import pandas as pd
import numpy as np

In [4]:
df_densidad = pd.read_csv('../data/densidad.csv')
df_demographics = pd.read_csv('../data/demographics.csv')
df_accidentes = pd.read_csv('../data/accidentes.csv')


In [5]:
df_densidad.rename(columns={'id_distrito':'cod_distrito'}, inplace=True)

In [6]:
df_demographics.rename(columns={'id_distrito':'cod_distrito'}, inplace=True)

In [7]:
#hago el merge para las tres tablas de una vez
import functools as ft
dfs = [df_accidentes, df_densidad, df_demographics]
accidentes = ft.reduce(lambda left, right: pd.merge(left, right, on='cod_distrito'), dfs)

In [8]:
accidentes.head()

id num_expediente       fecha      hora  \
0    0    2018S017842  2019-02-04  09:10:00   
1    1    2018S017842  2019-02-04  09:10:00   
2  207    2019S000349  2019-01-06  01:34:00   
3  208    2019S000349  2019-01-06  01:34:00   
4  256    2019S000480  2019-01-05  01:20:00   

                        localizacion numero  cod_distrito distrito  \
0          CALL. ALBERTO AGUILERA, 1      1             1   CENTRO   
1          CALL. ALBERTO AGUILERA, 1      1             1   CENTRO   
2  CUSTA. SAN VICENTE / CALL. BAILEN      1             1   CENTRO   
3  CUSTA. SAN VICENTE / CALL. BAILEN      1             1   CENTRO   
4    PLAZA. COLON / CALL. JORGE JUAN      1             1   CENTRO   

            tipo_accidente estado_meteorológico  ... mes dia      long  \
0         Colisión lateral            Despejado  ...   2   4 -3.706555   
1         Colisión lateral            Despejado  ...   2   4 -3.706555   
2         Colisión lateral            Despejado  ...   1   6 -3.721464   
3         Colisión lateral            Despejado  ...   1   6 -3.721464   
4  Colisión fronto-lateral            Despejado  ...   1   5 -3.690424   

         lat nombre_distrito  densidad_pob  edad_media  pob_men_18_perc  \
0  40.429592          Centro        252.34        43.5              8.5   
1  40.429592          Centro        252.34        43.5              8.5   
2  40.418879          Centro        252.34        43.5              8.5   
3  40.418879          Centro        252.34        43.5              8.5   
4  40.424641          Centro        252.34        43.5              8.5   

   pob_may_65_perc  pob_adulta_perc  
0             15.8             75.7  
1             15.8             75.7  
2             15.8             75.7  
3             15.8             75.7  
4             15.8             75.7  

[5 rows x 28 columns]

In [11]:
# heatmap de accidentes 2019-22

mapa_calor=folium.Map([40.416729, -3.703339], zoom_start=10)

data=accidentes[['lat', 'long']].values

mapa_calor.add_child(plugins.HeatMap(data, radius=10))

mapa_calor

In [12]:
#defino lista de meses para los que quiero hacer un heatmap 
df_month_list = []
for month in accidentes.mes.sort_values().unique():
    df_month_list.append(accidentes.loc[accidentes.mes == month, 
                                    ['lat', 
                                     'long', 
                                     'mes']].groupby(['lat', 
                                                        'long']).sum().reset_index().values.tolist())

In [13]:
#función para generar mapa base centrado sobre mi zona de estudio
def generateBaseMap(default_location=[40.416729, -3.703339], default_zoom_start=11):
    
    base_map = folium.Map(location=default_location, 
                          control_scale=True, 
                          zoom_start=default_zoom_start)
    
    return base_map

In [14]:
#genero un heatmap dinámico por meses
base_map = generateBaseMap(default_zoom_start=11) # crea mapa

HMWT(df_month_list, 
     radius=5, 
     gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, 
     min_opacity=0.5, 
     max_opacity=0.8, 
     use_local_extrema=True).add_to(base_map) # datos pata heatmap con tiempo


base_map  # representa

In [16]:
base_map.save('../img/mapa.mp4') # guarda el heatmap en mp4